# Gradient Boosting machine connected in series to the CNN

### Load dataset

In [1]:
import pandas as pd
import numpy as np

filepath = '/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/data/input/processed'
material_name = 'ten_materials'

# Read ten materrials
ds = pd.read_pickle(f'{filepath}/{material_name}.pkl.gz')

# read CNN processed df
cnn_processed_df = pd.read_csv('/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/data/output/CNN_H_preds_16-Sep-2023_06:55_Uhr_score_2.86.csv')
cnn_processed_df['material'] = ds['material'].copy()


/tmp/ipykernel_403/2222242364.py:11: DtypeWarning: Columns (256) have mixed types. Specify dtype option on import or set low_memory=False.
  cnn_processed_df = pd.read_csv('/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/data/output/CNN_H_preds_16-Sep-2023_06:55_Uhr_score_2.86.csv')


### Build new dataframe

In [2]:
print(f"{ds.shape = }")
print(f"{cnn_processed_df.shape = }")

#print(ds['material'])

ds = ds.drop(columns=[c for c in ds if c.startswith("H_t")])
#print(f"{pd.unique(ds["material"]) =} ")
#print(f"{pd.unique(cnn_processed_df["material"]) = } ")


ds['ploss'] = np.log(ds['ploss'])
ds['freq'] = np.log(ds['freq'])

# bring both dataframes together
ds = pd.concat([ds, cnn_processed_df.drop(columns= ['material'])], axis=1)
print(f"{ds.shape = }")


print(f"{list(ds.columns) = }")

#ds["material"] = ds["material"].astype(str)

#print(pd.unique(ds["material"]))


ds.shape = (186747, 2052)
cnn_processed_df.shape = (186747, 257)
ds.shape = (186747, 1284)
list(ds.columns) = ['B_t_0', 'B_t_1', 'B_t_2', 'B_t_3', 'B_t_4', 'B_t_5', 'B_t_6', 'B_t_7', 'B_t_8', 'B_t_9', 'B_t_10', 'B_t_11', 'B_t_12', 'B_t_13', 'B_t_14', 'B_t_15', 'B_t_16', 'B_t_17', 'B_t_18', 'B_t_19', 'B_t_20', 'B_t_21', 'B_t_22', 'B_t_23', 'B_t_24', 'B_t_25', 'B_t_26', 'B_t_27', 'B_t_28', 'B_t_29', 'B_t_30', 'B_t_31', 'B_t_32', 'B_t_33', 'B_t_34', 'B_t_35', 'B_t_36', 'B_t_37', 'B_t_38', 'B_t_39', 'B_t_40', 'B_t_41', 'B_t_42', 'B_t_43', 'B_t_44', 'B_t_45', 'B_t_46', 'B_t_47', 'B_t_48', 'B_t_49', 'B_t_50', 'B_t_51', 'B_t_52', 'B_t_53', 'B_t_54', 'B_t_55', 'B_t_56', 'B_t_57', 'B_t_58', 'B_t_59', 'B_t_60', 'B_t_61', 'B_t_62', 'B_t_63', 'B_t_64', 'B_t_65', 'B_t_66', 'B_t_67', 'B_t_68', 'B_t_69', 'B_t_70', 'B_t_71', 'B_t_72', 'B_t_73', 'B_t_74', 'B_t_75', 'B_t_76', 'B_t_77', 'B_t_78', 'B_t_79', 'B_t_80', 'B_t_81', 'B_t_82', 'B_t_83', 'B_t_84', 'B_t_85', 'B_t_86', 'B_t_87', 'B_t_88', 'B_t_89',

In [3]:
"""Run linear regression with regularization training"""
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression, Ridge
from sklearn.ensemble import RandomForestRegressor, HistGradientBoostingRegressor, GradientBoostingRegressor, VotingRegressor, ExtraTreesRegressor
from tqdm import tqdm
from pprint import pprint
from utils.experiments import get_stratified_fold_indices, PROC_SOURCE, get_bh_integral_from_two_mats
from utils.metrics import calculate_metrics
import xgboost as xgb

pd.set_option("display.max_columns", None)


def objective(trial):

    n_estimators = trial.suggest_int('n_estimators', 100, 800)
    # 429 is best
    print(f'{n_estimators = }')
    criterion = trial.suggest_categorical('criterion', ['squared_error'])
    print(f"{criterion = }")
    learning_rate = trial.suggest_float('learning_rate', 0.01, 0.5)
    # 0.12 is best
    print(f"{learning_rate = }")
    
    exp_log = {}
    for material_lbl, mat_df in tqdm(ds.groupby("material"), desc="Train across materials"):

        full_b = mat_df.loc[:, [f"B_t_{k}" for k in range(1024)]].to_numpy()
        dbdt = full_b[:, 1:] - full_b[:, :-1]
        mat_df = mat_df.reset_index(drop=True)

        #full_h = mat_df.loc[:, [f"h_pred_{k}" for k in range(255)]].to_numpy()


        full_h = (
                cnn_processed_df.query("material == @material_lbl")
                .reset_index(drop=True)
                .drop(columns=["material"])
                .to_numpy()
            )
        print(f"{full_h = }")
        #dhdt = full_h[:, 1:] - full_h[:, :-1]
        mat_df['p_derived_from_h'] = get_bh_integral_from_two_mats(
            mat_df.freq, full_b[:, :: 1024 // full_h.shape[1]], full_h
        )
        

        

        #x_vec = np.linspace(0, 1023, 1024)
        #b_vec = []
        #for value in x_vec:
        #    b_vec.append(f'B_t_{int(value)}')
        #mat_df["b"] = mat_df[b_vec].values.tolist()

        #x_vec = np.linspace(0, 255, 256)
        #h_pred_vec = []
        #for value in x_vec:
        #    h_pred_vec.append(f'h_pred_{int(value)}')
        #mat_df["h_pred"] = mat_df[h_pred_vec].values.tolist()
        
        x_vec = None
        b_vec = None
        #mat_df['delta_b'] = mat_df['b'].map(lambda x: np.max(x) - np.min(x))

        # figure out integral_part 
        mat_df["time_s"] = mat_df["freq"].map(lambda x: np.linspace(0, 1/x, 1024))     
        
        mat_df["b_rms"] = np.apply_along_axis(lambda x: np.sqrt(np.mean(np.gradient(np.gradient(x))**2)), 1, full_b)
        mat_df["b_rmq"] = np.apply_along_axis(lambda x: np.sqrt(np.mean(np.gradient(np.gradient(x))**4)), 1, full_b)
        mat_df["b_peak"] = np.apply_along_axis(lambda x: max(np.gradient(np.gradient(x))), 1, full_b)
        

        mat_df["h_rms"] = np.apply_along_axis(lambda x: np.sqrt(np.mean(np.gradient(np.gradient(x))**2)), 1, full_h)
        mat_df["h_rmq"] = np.apply_along_axis(lambda x: np.sqrt(np.mean(np.gradient(np.gradient(x))**4)), 1, full_h)
        mat_df["h_peak"] = np.apply_along_axis(lambda x: max(np.gradient(np.gradient(x))), 1, full_h)

        # cross validation 'kfold'
        kfold_lbls = get_stratified_fold_indices(mat_df, 4)
        mat_df_proc = mat_df.assign(
            kfold=kfold_lbls,
            temp_square = mat_df['temp'] ** 2,
            b_rms = mat_df["b_rms"],
            b_rmq = mat_df["b_rmq"],
            b_peak = mat_df["b_peak"],
            h_rms = mat_df["h_rms"],
            h_rmq = mat_df["h_rmq"],
            h_peak = mat_df["h_peak"],
            p_derived_from_h=mat_df['p_derived_from_h']

            # more features imaginable (count of spikes e.g.)
        ).drop(
            columns=[c for c in mat_df if c.startswith("B_t_")] + ["material"] + ['time_s'] + [c for c in mat_df if c.startswith("h_pred_")] # + ['b'] + ['h_pred']
        )  # drop B curve

        #print(mat_df_proc.to_string())

        print(f"Finished data preparation")

        # training result container
        results_df = mat_df_proc.loc[:, ["ploss", "kfold"]].assign(pred=0)
        x_cols = [c for c in mat_df_proc if c not in ["ploss", "kfold"]]
        print(x_cols)
        for kfold_lbl, test_fold_df in mat_df_proc.groupby("kfold"):
            train_fold_df = (
                mat_df_proc.query("kfold != @kfold_lbl")
                .reset_index(drop=True)
                .drop(columns="kfold")
            )
            assert len(train_fold_df) > 0, "empty dataframe error"
            y = train_fold_df.pop("ploss")
            X = train_fold_df.loc[:, x_cols]

            print(f"Start setting up and fitting model")
            #mdl = xgb.XGBRegressor(n_estimators=n_estimators, learning_rate=learning_rate) #, max_depth=max_depth)
            mdl = GradientBoostingRegressor(n_estimators=n_estimators, criterion=criterion, learning_rate=learning_rate) # HistGradientBoostingRegressor() # RandomForestRegressor(n_estimators = 100) #LinearRegression() # Ridge()  # 
            mdl.fit(X.to_numpy(), y.to_numpy())
            pred = mdl.predict(test_fold_df.loc[:, x_cols].to_numpy())
            results_df.loc[results_df.kfold == kfold_lbl, "pred"] = pred


        print(results_df.to_string())
        # book keeping
        exp_log[material_lbl] = calculate_metrics(
            np.exp(np.abs(results_df.loc[:, "pred"])), np.exp(results_df.loc[:, "ploss"])
        )
    print(mdl.__class__.__name__)
    print(f"{n_estimators = }")
    print(f"{learning_rate = }")
    print(mdl.feature_importances_)
    
    print("Overall Score")
    score = pd.DataFrame(exp_log).T
    print(score)

    added_avg_abs_rel_err = score['avg-abs-rel-err'].sum()
    print('sum error')
    print(added_avg_abs_rel_err)
    
    # feature importances
    feat_importances = pd.Series(mdl.feature_importances_, index=x_cols)
    feat_importances.nlargest(20).plot(kind='barh')
    
    return added_avg_abs_rel_err

In [4]:
import optuna

import sklearn.datasets
import sklearn.ensemble
import sklearn.model_selection
import sklearn.svm

# FYI: Objective functions can take additional arguments
# (https://optuna.readthedocs.io/en/stable/faq.html#objective-func-additional-args).



study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=1, n_jobs=1)
#print(study.best_trial)

[I 2023-09-27 13:10:13,139] A new study created in memory with name: no-name-a24a19d0-1b59-49ea-9f78-239e4e62af89


n_estimators = 635
criterion = 'squared_error'
learning_rate = 0.39858729240925206


Train across materials:   0%|          | 0/10 [00:00<?, ?it/s]

full_h = array([[ 0.71466775,  0.9092836 ,  1.10397741, ...,  0.12552357,
         0.32275512,  0.51796732],
       [ 0.97526514,  1.18887056,  1.40025087, ...,  0.33675938,
         0.55052893,  0.76622001],
       [ 0.69608839,  0.94632301,  1.18784388, ..., -0.04359009,
         0.2052587 ,  0.45252796],
       ...,
       [ 3.31704362,  3.08107433,  1.98184849, ..., -1.00771749,
         8.97128078,  8.26807865],
       [ 3.48181539,  3.53568514,  2.30439007, ..., -1.08522534,
         9.12805258,  9.35526949],
       [ 3.7759862 ,  3.89821089,  2.51335448, ..., -0.18877671,
        11.31487931,  9.66356804]])
Finished data preparation
['freq', 'temp', 'p_derived_from_h', 'b_rms', 'b_rmq', 'b_peak', 'h_rms', 'h_rmq', 'h_peak', 'temp_square']
Start setting up and fitting model
Start setting up and fitting model
Start setting up and fitting model
Start setting up and fitting model


Train across materials:  10%|█         | 1/10 [05:19<47:54, 319.44s/it]

...

           ploss  kfold       pred
0       8.139454      0   8.514314
1       8.820697      3   8.566939
2       9.423833      3   9.455058
3       9.975472      2   9.577704
4      10.551083      2  10.359811
5      11.021512      2  10.832334
6      11.509719      3  11.660778
7      11.993238      0  11.919887
8       7.310840      2   7.544027
9       7.909863      1   7.853055
10      8.544368      3   8.690393
11      9.137662      2   8.915973
12      9.679597      0   8.653032
13     10.253218      1  10.065546
14     10.781129      0  10.620597
15     11.271052      0  11.096019
16     11.769856      0  11.870454
17     12.275522      2  12.977816
18     12.760757      1  13.269100
19      7.556207      2   7.465959
20      8.173183      2   8.095399
21      8.794989      0   9.266706
22      9.347086      0   9.587574
23      9.961587      2   9.597469
24     10.492509      3  10.558246
25     11.017348      0  11.636097
26     11.532493      3  11.807158
27     12.061015    

Train across materials:  60%|██████    | 6/10 [15:02<07:05, 106.32s/it]

           ploss  kfold       pred
0       8.001014      3   8.017774
1       8.641863      1   8.704848
2       9.203028      3   9.087353
3       9.791905      2  10.235139
4      10.341004      1  10.524264
5      10.858778      3  10.415037
6      11.391636      1  12.665057
7      11.897999      1  13.437301
8       7.755283      2   7.671775
9       8.342134      3   8.304923
10      8.922691      3   8.680843
11      9.470508      3   9.450493
12     10.034156      1  10.581964
13     10.592731      2  10.849279
14     11.129722      1  11.893817
15     11.658496      0  12.057554
16     12.196821      3   9.847177
17     12.668905      1  11.754776
18      7.316978      2   7.670929
19      7.955600      0   7.958346
20      8.569947      0   8.874111
21      9.142348      1   9.123487
22      9.723898      1   9.439664
23     10.279875      0  10.204799
24     10.852911      2  11.154305
25     11.399972      2  11.457236
26     11.950306      2  11.216531
27     12.438276    

Train across materials:  60%|██████    | 6/10 [16:16<10:51, 162.82s/it]
[W 2023-09-27 13:26:30,094] Trial 0 failed with parameters: {'n_estimators': 635, 'criterion': 'squared_error', 'learning_rate': 0.39858729240925206} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/.venv/lib/python3.10/site-packages/optuna/study/_optimize.py", line 200, in _run_trial
    value_or_values = func(trial)
  File "/tmp/ipykernel_403/741900246.py", line 118, in objective
    mdl.fit(X.to_numpy(), y.to_numpy())
  File "/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/.venv/lib/python3.10/site-packages/sklearn/base.py", line 1151, in wrapper
    return fit_method(estimator, *args, **kwargs)
  File "/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/.venv/lib/python3.10/site-packages/sklearn/ensemble/_gb.py", line 525, in fit
    n_stages = self._fit_stages(
  File "/home/nikolasf/Dokumente/01_git/30_Python/MC_UPB/

KeyboardInterrupt: 